 # 0184940黎慧婷——第三次作业

## 解析每个硕士生导师的详情内容

### 导入库

In [65]:
import re
import requests
from bs4 import BeautifulSoup
headers={'User-Agent': 'Mozilla/5.0 (Windows NT 6.1; WOW64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/78.0.3904.108 Safari/537.36'}
import pandas
import pandas as pd 

### 将多页中的教师链接提取出来

In [66]:
detail_urls=[]
base_url='http://finance.jxufe.edu.cn/news-list-shuodao-{}.html'
for x in range(0,4):
  url = base_url.format(x)
  resp=requests.get(url)
  html = resp.text
  soup=BeautifulSoup(html,'lxml')
  lis=soup.find('div',class_='bd_listabc').find_all('li')
  for li in lis:
        detail_url=li.find('a')['href']
        detail_urls.append(detail_url)   
print(detail_urls)

['http://finance.jxufe.edu.cn/news-show-3097.html', 'http://finance.jxufe.edu.cn/news-show-1347.html', 'http://finance.jxufe.edu.cn/news-show-1348.html', 'http://finance.jxufe.edu.cn/news-show-1349.html', 'http://finance.jxufe.edu.cn/news-show-2066.html', 'http://finance.jxufe.edu.cn/news-show-1346.html', 'http://finance.jxufe.edu.cn/news-show-1343.html', 'http://finance.jxufe.edu.cn/news-show-1345.html', 'http://finance.jxufe.edu.cn/news-show-1344.html', 'http://finance.jxufe.edu.cn/news-show-3085.html', 'http://finance.jxufe.edu.cn/news-show-1342.html', 'http://finance.jxufe.edu.cn/news-show-1341.html', 'http://finance.jxufe.edu.cn/news-show-3097.html', 'http://finance.jxufe.edu.cn/news-show-1347.html', 'http://finance.jxufe.edu.cn/news-show-1348.html', 'http://finance.jxufe.edu.cn/news-show-1349.html', 'http://finance.jxufe.edu.cn/news-show-2066.html', 'http://finance.jxufe.edu.cn/news-show-1346.html', 'http://finance.jxufe.edu.cn/news-show-1343.html', 'http://finance.jxufe.edu.cn/n

### 硕士生导师详细简介

#### 所有的内容都在strong标签下，需要对其进行提取

In [67]:
def get_value(key,html):
    pattern='%s</strong>.*?：(.*?)</p>' % key
    searchObj=re.search(pattern,html)
    value=searchObj.group(1)
    return(value)

#### 获取strong标签下面的自我简介信息

In [68]:
def get_zwjj(key,html):
    self_intro = re.findall(r'自我简介(.*?)科研成果', html)
    self_intro_text = re.sub(r'</p>','\n',self_intro[0])
    self_intro_text_clear = re.sub(r'<(.*?)>','', self_intro_text).replace("&nbsp;","").replace("\n"," ").strip()
    return self_intro_text_clear

#### 获取strong标签下面的科研成果信息

In [69]:
def get_kycg(key,html):
    sci = re.findall(r'<span>科研成果(.*?)版权所有',html,re.S)
    sci_text = re.sub(r'</p>','\n',sci[0])
    sci_text_clear = re.sub(r'<(.*?)>','', sci_text).replace("&nbsp;","").replace("\n"," ").strip("：").strip()
    return sci_text_clear

#### 将硕士生导师的信息追加到字典中

In [73]:
def parse_detail_url(html):
    xm = get_value('姓　　名',html)
    xb = get_value('性　　别',html)
    csny = get_value('出生年月',html)
    zzmm = get_value('政治面貌',html)
    byyx = get_value('毕业院校',html)
    byzy = get_value('毕业专业',html)
    zw = get_value('职　　务',html)
    zc = get_value('职　　称',html)
    yx = get_value('邮&nbsp; &nbsp; &nbsp; &nbsp;箱',html)
    zwjj = get_zwjj('自我简介',html)
    kycg = get_kycg('科研成果',html)
    teacher_into = {'姓名':xm,
                    '性别':xb,
                    '出生年月':csny,
                    '政治面貌':zzmm,
                    '毕业院校':byyx,
                    '毕业专业':byzy,
                    '职务':zw,
                    '职称':zc,
                    '邮箱':yx,
                    '自我简介':zwjj,
                    '科研成果':kycg
                               }
    return(teacher_into)

#### 定义主函数

In [74]:
shuodao_list = []
def fail_list(detail_urls):
    fail_list = []
    for i in range(len(detail_urls)):
        t = requests.get(detail_urls[i]).text
        try:
            parse_detail_url(t)
            a=parse_detail_url(t)
            shuodao_list.append(a)
        except:
           fail_list.append(i)
    return fail_list 
fail_list(detail_urls)
shuodao_list
pd.DataFrame.from_dict(shuodao_list)
df =  pd.DataFrame.from_dict(shuodao_list)

In [75]:
df

姓名 性别 出生年月  政治面貌    毕业院校  \
0                                                  曹邓  女       中共党员  江西财经大学   
1                                                 陈春霞  女         群众  江西财经大学   
2                                                 陈家洪  男       中共党员  江西财经大学   
3                                                 胡少勇  男       中共党员  华东师范大学   
4                                                 李思敏  男       中共党员           
5                                                  曹邓  女       中共党员  江西财经大学   
6                                                 陈春霞  女         群众  江西财经大学   
7                                                 陈家洪  男       中共党员  江西财经大学   
8                                                 胡少勇  男       中共党员  华东师范大学   
9                                                 李思敏  男       中共党员           
10                                                刘兴华  男       中共党员    厦门大学   
11  吕江林<img style="float:right;padding-left:10px;"...  男       中共党员  中南财经大学   
12  寿晖<img width="107" height="160" style="float:r...  男                      
13                                                孙爱琳  女       中共党员    浙江大学   
14                                                 汪洋  男       中共党员  上海财经大学   
15                                                 王辉  男       中共党员  江西财经大学   
16                                                王清生  男         群众    云南大学   
17                                                 杨荣  女       中共党员  江西财经大学   
18                                                杨玉凤  女       民主党派  江西财经大学   
19                                                邹朋飞  男         群众    暨南大学   
20                                                曾鸿志  男         党员    天津大学   

            毕业专业          职务      职称  \
0            管理学                  教授   
1            金融学               教授/硕导   
2   经济统计（证券研究方向）               教授/硕导   
3            精算学         副院长     副教授   
4                        系主任     副教授   
5            管理学                  教授   
6            金融学               教授/硕导   
7   经济统计（证券研究方向）               教授/硕导   
8            精算学         副院长     副教授   
9                        系主任     副教授   
10          世界经济         副院长   教授/博导   
11           经济学  应用金融研究中心主任   教授/博导   
12                                     
13         政治经济学               教授、硕导   
14           金融学               教授/博导   
15           财政学               教授/硕导   
16      概率论与数理统计                  讲师   
17           金融学               教授、硕导   
18           金融学               教授/硕导   
19           金融学    货币银行系副主任  副教授/硕导   
20       投资经济管理学                 副教授   

                                                   邮箱  \
0                                laotoutou@aliyun.com   
1                                     new9360@163.com   
2                                      jxmcjh@126.com   
3                                     45022251@qq.com   
4                                jxcdzqtzxlsm@126.com   
5                                laotoutou@aliyun.com   
6                                     new9360@163.com   
7                                      jxmcjh@126.com   
8                                     45022251@qq.com   
9                                jxcdzqtzxlsm@126.com   
10                                    lxh7572@126.com   
11                                    ljl5983@126.com   
12                                13970014516@163.com   
13                                    sal6660@126.com   
14                              wangyang@jxufe.edu.cn   
15  “保险学”；“人身保险”；“责任保险”；“保险经营管理”；“保险营销学”；“风险管理”；“证...   
16                           ynuwangqingsheng@163.com   
17                               yonghongyang@163.com   
18                                  xialuoren@126.com   
19                                 Pengfeizou@163.com   
20                                    18409495@qq.com   

                                                 自我简介  \
0   一、开设课程：保险学原理、财产保险、保险中介管理、保险实务研究、商业保险理论与研究、财产保险...   
1   开设课程本科生主讲的主要课程有：《货币银行学》、《国际金融》《金融企业会计》、《投资项目评估...   
2    